In [283]:
from dotenv import load_dotenv
import src.query as query
import src.folium as fl
import src.data as dt
from pymongo import GEOSPHERE
import pandas as pd
import os
from src.variables import Variables as Var
from pymongo import MongoClient
import src.stakeholders as sh


In [3]:
%load_ext autoreload
%autoreload 2


In [4]:
load_dotenv('.env')

True

# 1. Connection to MongoDB database and Collection creation

In [5]:
conn = MongoClient("localhost:27017")
db = conn.get_database("ironhack")

* `offices` is a collection created for coworking spaces, i.e. location candidates.

* `helsinki_places` is a collection to save all the places queried.

In [6]:
offices = db['offices']

In [7]:
helsinki_places = db['helsinki_places']

# 2. Data collection

### Load token for foursqueare and Google APIs

In [8]:
client_id = os.getenv("FOURSQUARE_CLIENT_ID")
client_secret = os.getenv("FOURSQUARE_CLIENT_SECRET")

In [9]:
google_api = os.getenv("GOOGLE_PLACES")

### Establish candidates

These are the coordinates for our selected city: **Helsinki**

In [10]:
city_lat = Var.CITY_LAT
city_lon =  Var.CITY_LON
radius = Var.RADIUS

All coworking spaces as list of initial candidates

In [13]:
data_office = query.foursquare_query(city_lat, city_lon, 'coworking_space', radius, client_id, client_secret)



In [14]:
candidates = dt.read_foursquare_response(data_office, 'coworking_space')

Let's insert them to our brand new collection in MongoDb

In [15]:
x = offices.insert_many(candidates)

In [16]:
offices.find_one()

{'_id': ObjectId('5fafe7f65143de9ede25a204'),
 'type': 'coworking_space',
 'name': 'Tiedekulma / Think Corner',
 'location': {'coordinates': [24.948465, 60.169746], 'type': 'Point'}}

Let's create the Point for each office

In [17]:
offices.create_index([('location', GEOSPHERE)])

'location_2dsphere'

Now, let's plot the candidates to get a picture of their locations

In [447]:
map_candidates = fl.create_map(city_lat, city_lon)

In [448]:
for candidate in candidates:
    lat = candidate['location']['coordinates'][1]
    lon = candidate['location']['coordinates'][0]
    
    fl.add_marker_icon(map_candidates, lat, lon, 'blue','fa','building','white',candidate['name'], True)
    
    

In [449]:
map_candidates

In [485]:
map_candidates.save('output/candidates_map.html')

### Venus Search

#### Start-up Tech Companies

Search via Foursquare API

In [22]:
data_tech = query.foursquare_query(city_lat, city_lon, 'tech_startup', radius, client_id, client_secret)

Get a list of companies

In [23]:
tech_companies_list = dt.read_foursquare_response(data_tech, 'tech_startup')

Insert those documents in our collection `helsinki_places`

In [24]:
x = helsinki_places.insert_many(tech_companies_list)

And create index for GeoJson

In [25]:
helsinki_places.create_index([('location', GEOSPHERE)])

'location_2dsphere'

Now, let's find matches for each candidate and add to `offices` number of matches.

In [26]:
dt.find_matches_points(offices, helsinki_places, Var.TECH_COMP, 'tech_startup')

#### Starbucks

Search via Google Places API, using 'Find Place' which returns only one match.

For all candidates, we perform a query to find nearest Starbucks and get unique matches in a list.

In [27]:
starbucks_list = dt.find_all_google_places(offices, 'Starbucks', 50, google_api)


List of places is inserted to collection

In [ ]:
x = helsinki_places.insert_many(starbucks_list)
helsinki_places.create_index([('location', GEOSPHERE)])

And now perform matches based on distance defined in variables.py

In [28]:
dt.find_matches_points(offices, helsinki_places, Var.STARBUCKS_DISTANCE, 'Starbucks')

#### Preschool places

Search via Foursquare API. Similar approach as for finding tech companies.

In [29]:
preschool_data = query.foursquare_query(city_lat, city_lon, 'preschool', radius, client_id, client_secret)


In [30]:
preschools_list = dt.read_foursquare_response(preschool_data, 'preschools')
x = helsinki_places.insert_many(preschools_list)
dt.find_matches_points(offices, helsinki_places, Var.PRESCHOOL_DISTANCE, 'preschools')

#### Night-clubs

Search via Foursquare API. Similar approach as for finding tech companies.

In [31]:
disco_data = query.foursquare_query(city_lat, city_lon, 'night_club', radius, client_id, client_secret)


In [32]:
disco_list = dt.read_foursquare_response(disco_data, 'night_club')
x = helsinki_places.insert_many(disco_list)
dt.find_matches_points(offices, helsinki_places, Var.DISCO_DISTANCE, 'night_club')

#### Design Studios


Search via Google Places API. Similar approach as for finding Starbucks.

In [259]:
design_com_list = dt.find_all_google_places(offices, 'Design company', 300, google_api)

In [261]:
x = helsinki_places.insert_many(design_com_list)
helsinki_places.create_index([('location', GEOSPHERE)])

'location_2dsphere'

In [262]:
dt.find_matches_points(offices, helsinki_places, Var.STARBUCKS_DISTANCE, 'Design company')

#### Vegan Restaurants

Search via Foursquare API. Similar approach as for finding tech companies.

In [35]:
vegan_data = query.foursquare_query(city_lat, city_lon, 'vegan_rest', radius, client_id, client_secret)


In [36]:
vegan_list = dt.read_foursquare_response(vegan_data, 'vegan_rest')
x = helsinki_places.insert_many(vegan_list)
dt.find_matches_points(offices, helsinki_places, Var.VEGAN_DISTANCE, 'vegan_rest')

#### Pet Groomers

Search via Foursquare API. Similar approach as for finding tech companies.

In [37]:
pet_groomer_list = dt.find_all_google_places(offices, 'pet groomer', 50, google_api)


In [38]:
x = helsinki_places.insert_many(pet_groomer_list)
helsinki_places.create_index([('location', GEOSPHERE)])
dt.find_matches_points(offices, helsinki_places, Var.PET_GROOMER_DISTANCE, 'pet groomer')

#### Basketball stadiums

Search via Foursquare API. Similar approach as for finding tech companies.

In [42]:
basket_data = query.foursquare_query(city_lat, city_lon, 'basket_stadium', radius, client_id, client_secret)

In [43]:
basket_list = dt.read_foursquare_response(basket_data, 'basket_stadium')
x = helsinki_places.insert_many(basket_list)
dt.find_matches_points(offices, helsinki_places, Var.BASKET_STADIUM_DISTANCE, 'basket_stadium')

#### Travel to Airport

Search via Google Maps API

For each candidate, it is queried time travel from the coworking space location to Helsinki-Vantaa Airport, both by driving and by public transport.

For uniform time travels, travel route is queried for a regular weekday with arrival time at 12:00. As per API request, arrival time is needed to be input as seconds since 1st Jan 1970.

In [100]:
time = query.get_time_for_google(Var.TIME_CALC_YEAR, Var.TIME_CALC_MONTH, Var.TIME_CALC_HOUR, Var.TIME_CALC_DAY)

dt.get_travel_time(offices, Var.AIRPORT_LAT, Var.AIRPORT_LON, google_api, time)


## Summary

In [18]:
df = pd.DataFrame(offices.find({}))

In [474]:
df.head(2)

_id             type                       name  \
0  5fafe7f65143de9ede25a204  coworking_space  Tiedekulma / Think Corner   
1  5fafe7f65143de9ede25a205  coworking_space          Spalt PR Helsinki   

                                            location  tech_startup  Starbucks  \
0  {'coordinates': [24.948465, 60.169746], 'type'...            26          0   
1  {'coordinates': [24.95028953736944, 60.1678398...            26          0   

   preschools  night_club  vegan_rest  pet groomer  basket_stadium  driving  \
0           1          11           2            0               6     26.3   
1           0           7           4            0               5     27.2   

   transit  Design company  
0     35.0               0  
1     39.0               0

In [20]:
df_places = pd.DataFrame(helsinki_places.find({}))

In [475]:
df_places.head(2)

_id          type         name  \
0  5fafe8175143de9ede25a249  tech_startup    Meetin.gs   
1  5fafe8175143de9ede25a24a  tech_startup  Osuma.fi HQ   

                                            location place_id  
0  {'coordinates': [24.932639703932836, 60.168104...      NaN  
1  {'coordinates': [24.936691031806237, 60.169992...      NaN

Backup saving

In [276]:
df.to_csv('data/backup.csv', index=False)

# 3. Find best Candidate

Now, let's find the best suitable coworking space.

## Create our employees

First, let's create our collection of stakeholders, i.e. the employees plus the office dog.

In [79]:
stakeholders = sh.create_stakeholders()

Now let's assign a child to 30% of employees, i.e. 26 persons approx.

In [80]:
stakeholders = sh.assign_child(stakeholders, Var.PARENTS_CHILD)

In [81]:
stakeholders[0:5]

## Scoring and Sorting

Now, let's score each candidate based on their geolocation results.

But first, let's take a look at the columns to get a feeling of the findings.

In [82]:
df.describe()

tech_startup  Starbucks  preschools  night_club  vegan_rest  \
count     69.000000  69.000000   69.000000   69.000000   69.000000   
mean      12.173913   0.072464    0.550725    4.217391    0.826087   
std       12.074471   0.261154    0.697395    6.803696    1.282880   
min        0.000000   0.000000    0.000000    0.000000    0.000000   
25%        2.000000   0.000000    0.000000    0.000000    0.000000   
50%        6.000000   0.000000    0.000000    0.000000    0.000000   
75%       24.000000   0.000000    1.000000    7.000000    1.000000   
max       36.000000   1.000000    2.000000   28.000000    6.000000   

       pet groomer  basket_stadium    driving    transit  Design company  
count    69.000000       69.000000  69.000000  69.000000       69.000000  
mean      0.405797        5.231884  24.315942  47.289855        0.130435  
std       0.810208        0.710114   4.336291  10.007485        0.339248  
min       0.000000        3.000000  14.000000  25.800000        0.000000  
25%       0.000000        5.000000  21.200000  40.800000        0.000000  
50%       0.000000        5.000000  25.500000  47.400000        0.000000  
75%       1.000000        6.000000  27.200000  54.500000        0.000000  
max       3.000000        6.000000  30.800000  72.600000        1.000000

Score is applied as explanied in Readme

In [479]:
df_score = sh.get_all_scores(df, stakeholders)

Here it is top3

In [480]:
df_score.head(3)

_id                name  \
10  5fafe7f65143de9ede25a20e           Epicenter   
27  5fafe7f65143de9ede25a21f  Terveystalo Piazza   
28  5fafe7f65143de9ede25a220        Four Reasons   

                                             location  design_score  \
10  {'coordinates': [24.94577562322455, 60.1698553...             0   
27  {'coordinates': [24.930631, 60.169916], 'type'...             0   
28  {'coordinates': [24.929534196853634, 60.168788...             0   

    school_score  tech_score  starbucks_score  airport_score  party_score  \
10           535         225              500          433.0         1935   
27           535         225              500          401.0         1935   
28           535         225              500          392.0         1935   

    vegan_score  basket_score  dog_score   total  
10          100            10          0  3738.0  
27          100            10          0  3706.0  
28          100            10          5  3702.0

And bottom3

In [477]:
df_score.tail(3)

_id                name  \
41  5fafe7f65143de9ede25a22d         Eckerö Line   
58  5fafe7f65143de9ede25a23e         Moonsoft Oy   
67  5fafe7f65143de9ede25a247  Ahti Business Park   

                                             location  design_score  \
41  {'coordinates': [24.920848013578677, 60.154510...             0   
58  {'coordinates': [24.820141111789763, 60.179604...             0   
67  {'coordinates': [24.774798229336735, 60.166870...             0   

    school_score  tech_score  starbucks_score  airport_score  party_score  \
41             0           0                0          224.0            0   
58             0           0                0          191.0            0   
67             0           0                0          112.0            0   

    vegan_score  basket_score  dog_score  total  
41            0            10          0  234.0  
58            0            10          0  201.0  
67            0            10          0  122.0

And the winner is... [Epicenter](https://weareepicenter.com/helsinki/), a coworking space located at the heart of Helsinki city center.

In [482]:
winner_data =list(offices.find({'name' : winner_name}, ))[0]
winner_name = (df_score['name'].head(1).iloc[0])
winner_data

{'_id': ObjectId('5fafe7f65143de9ede25a20e'),
 'type': 'coworking_space',
 'name': 'Epicenter',
 'location': {'coordinates': [24.94577562322455, 60.169855303538235],
  'type': 'Point'},
 'tech_startup': 28,
 'Starbucks': 1,
 'preschools': 1,
 'night_club': 12,
 'vegan_rest': 5,
 'pet groomer': 0,
 'basket_stadium': 6,
 'driving': 26.7,
 'transit': 33.3,
 'Design company': 0}

# Visualization

Let's create pretty maps to justify our decision to the rest of employees.

### Requirements fulfill

Let's create a map showing the venues which met the distance criteria, and therefore provide the points to win for our new office venue.

In [451]:
win_name = winner_data['name']
win_lon = winner_data['location']['coordinates'][0]
win_lat = winner_data['location']['coordinates'][1]

In [452]:
map_winner = fl.create_map(win_lat, win_lon)

First, let's add the win location

In [453]:
fl.add_marker_icon(map_winner, win_lat, win_lon, 'red','fa','star','white',win_name, True) #here we add the winner


And then add all the venues

In [454]:
fl.add_map_matches(map_winner, winner_data, helsinki_places, Var.PRESCHOOL_DISTANCE, 'preschools', 'blue', 'custom','src/img/baby.png', 'white', False)
fl.add_map_matches(map_winner, winner_data, helsinki_places, Var.DISCO_DISTANCE, 'night_club', 'black', 'custom','src/img/party.png', 'white', False)
fl.add_map_matches(map_winner, winner_data, helsinki_places, Var.VEGAN_DISTANCE, 'vegan_rest', 'green','custom','src/img/vegan.png', 'white', False)
fl.add_map_matches(map_winner, winner_data, helsinki_places, Var.BASKET_STADIUM_DISTANCE, 'basket_stadium', 'orange', 'custom','src/img/basketball.png','white', False)
fl.add_map_matches(map_winner, winner_data, helsinki_places, Var.PET_GROOMER_DISTANCE, 'pet groomer', 'brown','custom','src/img/dog.png','white', False)
fl.add_map_matches(map_winner, winner_data, helsinki_places, Var.STARBUCKS_DISTANCE, 'Starbucks', 'brown','custom', 'src/img/starbucks.png','white', False)
fl.add_heat_map(helsinki_places, map_winner, 'tech_startup')
folium.LayerControl(collapsed = False).add_to(map_winner)

In [455]:
map_winner

In [484]:
map_winner.save('output/nearby_map.html')

### Airport travel time

Initially, we set an ideal travel time to airport of 20 minutes by car, or 40 minutes by public transport. Venues exceeding those number were penalized accordingly. 

In [464]:
map_winner3 = fl.create_map(win_lat, win_lon)
fl.add_marker_icon(map_winner3, win_lat, win_lon, 'red','fa','star','white',win_name, True)
fl.add_marker_icon(map_winner3, Var.AIRPORT_LAT, Var.AIRPORT_LON, 'red','custom','src/img/airport.png','white','Helsinki-Vantaa Airport', True)
fl.add_marker_icon(map_winner3, Var.TRAIN_LAT, Var.TRAIN_LON, 'red','custom','src/img/train.png','white','Rautatientori Station', True)

In [465]:
car_airport = winner_data['driving']
train_airport = winner_data['transit']

text = f'Time to airport by car: {car_airport} min\nTime to airport by train: {train_airport} min'

In [466]:
fl.add_pop_up(text, map_winner3,Var.AIRPORT_LAT, Var.AIRPORT_LON)

In [467]:
map_winner3

In [483]:
map_winner3.save('output/2airport_map.html')

### Distance to closest venues

On the first map, you may missed a location of a **design company** to please our designer or a **dog groomer** for 'Pepe'.

In [460]:
map_winner2 = fl.create_map(win_lat, win_lon)
fl.add_marker_icon(map_winner2, win_lat, win_lon, 'red','fa','star','white',win_name, True)

In [461]:
fl.add_closest(map_winner2, winner_data, helsinki_places, 'pet groomer', 'brown', 'custom', 'src/img/dog.png', 'white',False)
fl.add_closest(map_winner2, winner_data, helsinki_places, 'Design company', 'brown', 'custom', 'src/img/design.png', 'white',False)
folium.LayerControl(collapsed = False).add_to(map_winner2)

Unfortunately, our office does not meet the minimum required distance for those two venues. Nevertheless, below you can find the closest venues along with its distance to our office. Not that bad either right?

In [462]:
map_winner2

In [486]:
map_winner2.save('output/closest_map.html')

## Competitor

And finally, let's find out where is located our successfull competitor **Supercell**. It is 1.8 km away.

In [471]:
competitor = 'Supercell'
map_winner4 = fl.create_map(win_lat, win_lon)
fl.add_marker_icon(map_winner4, win_lat, win_lon, 'red','fa','star','white',win_name, True)
fl.locate_competitor(map_winner4, helsinki_places, competitor, win_lat, win_lon)


In [472]:
map_winner4

In [487]:
map_winner4.save('output/competitor_map.html')

# 4. Saving Dataframes

In [506]:
df.to_csv('data/candidates.csv', index=False)
df_score.to_csv('data/score.csv', index=False)
df_places.to_csv('data/places.csv', index=False)